# The DaCHS Prototype for Persistent TAP Uploads

From its beginning, TAP has let users upload their tables; but these uploads only existed for the duration of the request.  Having more persistent user-uploaded tables, however, has quite a few interesting applications.

Inspired by Pat Dowler's 2018 Interop talk on youcat, 
https://wiki.ivoa.net/internal/IVOA/InterOpNov2018DAL/tap-youcat.pdf, I have made a simple implementations for persistent tables in DaCHS.  This notebook shows how this can be operated even without support for it in pyVO.

**Note:** This is certainly not what will eventually become a standard.  Do not do large implementations against what is discussed here.

This is an update of the notebook I published with https://blog.g-vo.org/a-proposal-for-persistent-tap-uploads.html


In [ ]:
import pyvo
import requests
# get a table to upload; this must be a VOTable
to_upload = requests.get("https://docs.g-vo.org/upload_for_regressiontest.vot")

In [ ]:
GAVO_TAP = "http://dc.g-vo.org/tap"
svc = pyvo.dal.TAPService(GAVO_TAP)

(If it bothers you, feel free to change the URL schema to https; but with http, you can watch what happens with ngrep, wireshark and its ilk without having to jump through too many hoops).

First, we need a VOTable to upload; let me pull one from the net.  The actual upload is a PUT request to a child of a *sibling* of VOSI tables; in the current implementation, that's `user_tables`.  The child name becomes the table name.

In [ ]:
res = requests.put(svc.baseurl+"/user_tables/my_upload", 
             data=to_upload.content,
             headers={"content-type": "application/x-votable+xml"})
(res.status_code, res.text)

For now, this returns an explanatory string.  I *think* I will change this with a redirect to the uploaded table's GET URL.  That returns a VOSI tableset (non-nerd speak: column metadata for the uploaded table).  Just use the URI you uploaded to, but do a GET instead of a PUT.  The scary bits are what is required to make pyVO parse this:

In [ ]:
import io
from pyvo.io import vosi

def parse_vosi_table(source_data):
    return vosi.parse_tables(io.BytesIO(source_data)).get_first_table()

table_meta = parse_vosi_table(
    requests.get(svc.baseurl+"/user_tables/my_upload").content)
print([c.name for c in table_meta.columns])
print(table_meta.columns[0]. name, table_meta.columns[0].unit)

The main point of the exercise is that you can now run TAP queries against your table.  The user-uploaded tables are in the `tap_user` schema.

In [ ]:
svc.run_sync("SELECT raj2000, dej2000, jmag FROM tap_user.my_upload"
             " WHERE jmag>10")

This (ought to) work just like any other table.  For instance, you can run joins and all that:

In [ ]:
svc.run_sync("SELECT source_id FROM gaia.dr3lite JOIN tap_user.my_upload"
             " on (distance(ra, dec, raj2000, dej2000)<0.01)")

When done with the uploaded table, you should clean up after yourself by DELETE-ing the table URL:

In [ ]:
requests.delete(svc.baseurl+"/user_tables/my_upload").text

If you try to delete a table that does not exist, you get an error.  It looks somewhat unwieldy without an API, but it is a standards-compliant (DALI) error message.

In [ ]:
msg = requests.delete(svc.baseurl+"/user_tables/smallgaia").content
print("Don't look at this:", msg[300:])

from astropy.io import votable
import io

def extract_dali_error(msg):
    parsed = votable.parse(io.BytesIO(msg))
    return parsed.get_info_by_id("QUERY_STATUS").content

print("\nA future API will print this: '{}'".format(
    extract_dali_error(msg)))

As with PUT, a successful DELETE returns a little informative plain text string.  Again, I am not really sure if this is right.  Against PUT, it is still harder to say where this would sensibly redirect to.  Perhaps the table listing?  See below, though.

Once that's done (or after some time, in the case of this service seven days), the table is gone from the TAP service:

In [ ]:
try:
    svc.run_sync("SELECT COUNT(*) FROM tap_user.my_upload")
except pyvo.DALQueryError as exc:
    print(exc)

## Authenticated Operation

So, you wonder: Can anyone delete and query my tables?  Well, sort of, as long as you are anonymous – although they would have to guess your table name, and choosing an obvious table name is probably a bad idea because if it is obvious to some other person, too, you will overwrite each other's tables even if both of you are benevolent.  

Anyway, once you are authenticated, all these problems go away and you have a `tap_user` all for yourself.  Regrettably, there still is no federated authentication in astronomy, so you will in general have to obtain credentials per service.  For the service we run here, contact gavo@ari.uni-heidelberg.de for credentials.  Or use uptest/uptest – which of course you share with everyone reading this.

In [ ]:
session = pyvo.auth.AuthSession()
session.credentials.set_password("uptest", "uptest")
session.add_security_method_for_url(GAVO_TAP, "ivo://ivoa.net/sso#BasicAA")
auth_svc = pyvo.dal.TAPService(GAVO_TAP, session=session)

You can now do the table management as above, except you need to repeat the credentials in the requests call:

In [ ]:
requests.put(svc.baseurl+"/user_tables/my_upload", 
             data=to_upload.content,
             auth=("uptest", "uptest"),
             headers={"content-type": "application/x-votable+xml"}).text

## Creating Persistent Uploads From ADQL

An alternative way to create persistent tables (that also works for anonymous users) is through `CREATE TABLE`.  This would look like this:

In [ ]:
resp = auth_svc.run_sync("CREATE TABLE tap_user.smallgaia AS SELECT *"
                    " FROM gaia.dr3lite TABLESAMPLE(0.001)")

This returns an empty VOTable with the columns metadata of your new table.

In [ ]:
resp

## Inspecting Table Metadata

What you cannot do as anonymous: List the tables in your TAP uploads.  You to that by a GET against `user_tables`, and again you get back VOSI tables material:

In [ ]:
my_tables = vosi.parse_tables(io.BytesIO(
    requests.get(svc.baseurl+"/user_tables",
    auth=("uptest", "uptest")).content))

In particular, you now see the two tables you uploaded and can inspect their metadata:

In [ ]:
table_meta = list(my_tables.iter_tables())
print([t.name for t in table_meta])
print([(c.name, c.unit) for c in table_meta[0].columns])

Again, you can work table just as you would work with a built-in table.

In [ ]:
auth_svc.run_sync(
    "select avg(phot_bp_mean_mag-phot_rp_mean_mag) as avgcolor"
    " from tap_user.smallgaia"
    " where radial_velocity<20").to_table()

An anonymous user cannot see your table (or if they see a tap_user.smallgaia, it's something a joker has created to confuse people trying out this notebook).

In [ ]:
try:
    svc.run_sync(
        "select avg(phot_bp_mean_mag-phot_rp_mean_mag)"
        " from tap_user.smallgaia"
        " where radial_velocity<20").to_table()
except Exception as exc:
    print(exc)

This concluded what was discussed in the 2024 post http://blog.g-vo.org/a-proposal-for-persistent-tap-uploads.html (there have been some minor updates here).  The following sections describe new, vintage 2025 features.

## Prolonging a Table's Lifetime

As pointed out above, a service will discard a persistent upload after a certain time.  You can find out when this will be by GET-ing the ``destruction`` child of your table URI.  Again, pyVO doesn't have an API for that yet.

In [ ]:
import datetime
tableurl = svc.baseurl+"/user_tables/my_upload"
res = requests.put(tableurl, 
             data=to_upload.content,
             headers={"content-type": "application/x-votable+xml"})
cur_destruction = datetime.datetime.fromisoformat(
    requests.get(tableurl+"/destruction").text)
cur_destruction

This ought to be roughly a week from now for you.  If you would like to keep the table around for a bit longer, you can POST a DALI-style timestamp to the destruction endpoint (i.e., the URI you get that date from).  Let's say you want four extra years:

In [ ]:
new_destruction = cur_destruction+datetime.timedelta(days=4*365.25)
requests.post(tableurl+"/destruction", 
              {"DESTRUCTION": new_destruction.isoformat()}).text

The POST request returns the destruction time actually configured.  In this case, the service will not honour requests to extend the life time of a table beyond one year in the future; this is what you should see.  Admittedly, it is a bit strange to post a DESTRUCTION parameter to an endpoint already called destruction.

Well, we follow UWS here (although, yes, tables are no jobs and thus we don't *actually* do UWS).  UWS, in turn, did it like it did it to make it easy to operate this from a web browser form.  I'm not sure that argument alone would convince me today, but it's definitely better to retain the pattern once it's established if it's not entriely broken.

## Creating Indexes

Persistently uploaded tables can be large (to be entirely honest, on the test service there is currently no size limit enforced when you say CREATE TABLE; if you abuse that, there will be a size limit enforced in the future).  To have fast queries on large tables, databases need indexes.  You can create these by POST-ing to the index child of the table URL; just name the column you want indexed in an INDEX parameter (see above on the slightly odd call pattern):

In [ ]:
indexurl = tableurl+"/index"
res = requests.post(indexurl, {"INDEX": "Kmag"}, allow_redirects=False)
res

Since indexing can take quite a while, what you get back here is a UWS job URL (this is basically like async TAP).  Again, this will be hidden behind an API at some point.  Meanwhile, you can get the job URL from the server response and inspect the ``phase`` child of that job URL to see if the index is done computing (actually, we're doing here what's known as a “long poll” in VOSI; but never mind, there'll be a nice API for this eventually):

In [ ]:
requests.get(res.headers["Location"]+"/phase", {"WAIT": "-1"}).text

The net result should be that many queries involving Kmag would be a lot faster now.  We're talking orders of magnitudes for some interesting sorts of queries.

For this very small table, it's hard to contrive an example, though. You can see that an index *has been requested* in the table metadata:

In [ ]:
table_meta = parse_vosi_table(
    requests.get(svc.baseurl+"/user_tables/my_upload").content)
kmag_col = [c for c in table_meta.columns if c.name=="kmag"][0]
kmag_col.flags

Note that this indexed marking will already be there while the indexing job is still running.  The same goes for some more in-depth metadata on indexes.  The plain flag on the tableset is a bit too little if you actually want to know what sort of queries would profit from an index.  We will see examples in a moment.  Right now, let me mention that you can run a GET on the index endpoint, and that will give you some, let's say, debugging information.  I'm suggesting this should not be machine-readable but material useful to users wanting to see what is going on behind the scenes; the suggested representation is the SQL CREATE INDEX statements generated on behalf of the user.  In our case:

In [ ]:
print(requests.get(indexurl).text)

Special index types are particularly important in the case of spatial indexes, arguably the most important ones in astronomy.  When you use properly marked-up coordinates, the indexer should automatically use the right sort of index:

In [ ]:
requests.post(indexurl, {"INDEX": ["_RAJ2000", "_DEJ2000"]})

In [ ]:
print(requests.get(indexurl).text)

You are not really supposed to understand what the odd statements for the my_upload__RAJ2000__DEJ2000  index mean; but it's pretty clear that the box understood it's a spatial pair.

This particular implementation will refuse a spatial index (and use a normal one) when the coordinate types don't match.  For instance, if you mix equatorial and galactic:

In [ ]:
requests.post(indexurl, {"INDEX": ["_Glon", "_DEJ2000"]})
print(requests.get(indexurl).text)

– no magic expression is being created.  Since the sorts of magic required for certain sorts for columns and queries are strongly dependent on the backend database server, we don't say much more than “try to guess what's most useful based on the UCDs and types of the columns the user wants to index”.